# Homework 3
Julia Kaznowska <br>
Warsaw University of Technology <br>
Faculty of Mathematics and Information Science <br>
WB XAI tabular

## Importing libraries

In [66]:
import numpy as np
import pandas as pd
import random

random.seed(2137)

import warnings
warnings.filterwarnings("ignore")
pd.options.mode.chained_assignment = None

## Preparing variables (copied from previous hw)

### Handling missing values

In [67]:
data = pd.read_csv('housing.csv')

In [68]:
data.isnull().sum()

longitude               0
latitude                0
housing_median_age      0
total_rooms             0
total_bedrooms        207
population              0
households              0
median_income           0
median_house_value      0
ocean_proximity         0
dtype: int64

### Filling na

In [69]:
bedroom_mean = data['total_bedrooms'].mean()
data['total_bedrooms'].fillna(bedroom_mean, inplace=True)

### Adding variables

In [70]:
data["rooms_per_household"] = data["total_rooms"]/data["households"]
data["bedrooms_per_room"] = data["total_bedrooms"]/data["total_rooms"]
data["population_per_household"]=data["population"]/data["households"]

### Encoding categorical variables

In [71]:
X = data.drop(['median_house_value'], axis=1)
y = data.iloc[:,-5]

In [72]:
from sklearn.preprocessing import LabelEncoder

le = LabelEncoder()
X['ocean_proximity'] = le.fit_transform(X['ocean_proximity'])
X.head()

longitude  latitude  housing_median_age  total_rooms  total_bedrooms  \
0    -122.23     37.88                41.0        880.0           129.0   
1    -122.22     37.86                21.0       7099.0          1106.0   
2    -122.24     37.85                52.0       1467.0           190.0   
3    -122.25     37.85                52.0       1274.0           235.0   
4    -122.25     37.85                52.0       1627.0           280.0   

   population  households  median_income  ocean_proximity  \
0       322.0       126.0         8.3252                3   
1      2401.0      1138.0         8.3014                3   
2       496.0       177.0         7.2574                3   
3       558.0       219.0         5.6431                3   
4       565.0       259.0         3.8462                3   

   rooms_per_household  bedrooms_per_room  population_per_household  
0             6.984127           0.146591                  2.555556  
1             6.238137           0.155797                  2.109842  
2             8.288136           0.129516                  2.802260  
3             5.817352           0.184458                  2.547945  
4             6.281853           0.172096                  2.181467

### Splitting data

In [73]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X,y,test_size=0.2)

## Creating models

In [74]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
model1 = RandomForestRegressor(max_depth=7, n_estimators = 25, max_features="sqrt")
model2 = GradientBoostingRegressor(learning_rate = 0.2, max_features="sqrt")
model3 = DecisionTreeRegressor()

In [75]:
model1.fit(X_train, y_train)
model2.fit(X_train, y_train)
model3.fit(X_train, y_train);

### Checking performance

In [76]:
def print_scoring(model):
    train = cross_val_score(model, X_train, y_train, scoring = 'r2')
    test = r2_score(y_test, model.predict(X_test))
    print("Training data:", np.round(np.mean(train), 2))
    print("Test data:", np.round(test, 2))

In [77]:
from sklearn.model_selection import cross_val_score
from sklearn.metrics import r2_score
print("Random Forest:")
print_scoring(model1)
print("Gradient Boosting:")
print_scoring(model2)
print("Decision Tree:")
print_scoring(model3)

Random Forest:
Training data: 0.73
Test data: 0.73
Gradient Boosting:
Training data: 0.79
Test data: 0.78
Decision Tree:
Training data: 0.62
Test data: 0.63


After tuning hiperparameters the models have satisfying scorings. I chose `Gradient Boosting` as the best performing one, as it has the highest scorings. 

## Points from homework

### Model prediction

In [78]:
model2.predict(X_test.iloc[[312]])

array([98696.81030574])

In [79]:
y_test.iloc[[312]]

13550    67000.0
Name: median_house_value, dtype: float64

### Ceteris Paribus profiles for best model

In [80]:
import dalex as dx
gb_exp = dx.Explainer(model2, X_train, y_train, label = "Gradient Boosting")

Preparation of a new explainer is initiated

  -> data              : 16512 rows 12 cols
  -> target variable   : Parameter 'y' was a pandas.Series. Converted to a numpy.ndarray.
  -> target variable   : 16512 values
  -> model_class       : sklearn.ensemble._gb.GradientBoostingRegressor (default)
  -> label             : Gradient Boosting
  -> predict function  : <function yhat_default at 0x0000029C8DE48700> will be used (default)
  -> predict function  : Accepts pandas.DataFrame and numpy.ndarray.
  -> predicted values  : min = 1.37e+04, mean = 2.06e+05, max = 6.11e+05
  -> model type        : regression will be used (default)
  -> residual function : difference between y and yhat (default)
  -> residuals         : min = -2.66e+05, mean = 4.35e-12, max = 3.41e+05
  -> model_info        : package sklearn

A new explainer has been created!


In [81]:
cp_312_gb = gb_exp.predict_profile(X_test.iloc[[312]])
cp_312_gb.plot()

Calculating ceteris paribus: 100%|████████████████████████████████████████████████████| 12/12 [00:00<00:00, 299.94it/s]


As we can see, 6 of the variables used to explain the predicted value of the 312th observation have almost constant distribuation (changes happen only at left limits). General trends for non-constant observations are downward for `latitude` and `longitude` and upward for `housing_median_age`, `median_income`, `ocean_proximity` and `rooms_per_household`. The lowest prediction is a little bit less than 200k for the smallest `median_income`, whereas the highest price is about 550k for `longitude` around -122.5. 

### Ceteris Paribus profiles for other models

In [82]:
rf_exp = dx.Explainer(model1, X_train, y_train, label = "Random Forest")
dt_exp = dx.Explainer(model3, X_train, y_train, label = "Decision Tree")

Preparation of a new explainer is initiated

  -> data              : 16512 rows 12 cols
  -> target variable   : Parameter 'y' was a pandas.Series. Converted to a numpy.ndarray.
  -> target variable   : 16512 values
  -> model_class       : sklearn.ensemble._forest.RandomForestRegressor (default)
  -> label             : Random Forest
  -> predict function  : <function yhat_default at 0x0000029C8DE48700> will be used (default)
  -> predict function  : Accepts pandas.DataFrame and numpy.ndarray.
  -> predicted values  : min = 8.4e+04, mean = 2.06e+05, max = 4.94e+05
  -> model type        : regression will be used (default)
  -> residual function : difference between y and yhat (default)
  -> residuals         : min = -2.36e+05, mean = -79.1, max = 3.64e+05
  -> model_info        : package sklearn

A new explainer has been created!
Preparation of a new explainer is initiated

  -> data              : 16512 rows 12 cols
  -> target variable   : Parameter 'y' was a pandas.Series. Convert

In [83]:
cp_312_rf = rf_exp.predict_profile(X_test.iloc[[312]])
cp_312_dt = dt_exp.predict_profile(X_test.iloc[[312]])
cp_312_gb.plot([cp_312_rf, cp_312_dt])

Calculating ceteris paribus: 100%|████████████████████████████████████████████████████| 12/12 [00:00<00:00, 279.02it/s]


After adding CP-profiles for the other two models, we can see that both of them are mostly similar to `Gradient Boosting`, with `Random Forest` being a little bit closer than `Decision Tree`. <br>
All the models have different distributions when it comes to `longitude`. New models differ from `GB` for the `rooms_per_household` variable. `Decision Tree` varies significantly when it comes to `latitude` and `median_income` variables. <br>
Those results clearly show us that `Random Forest` model, having second best scoring has more similar CP profiles to the best model, than `Decision Tree`, which was third. It makes us happy, because it makes sense :) 